In [ ]:
!pip install --upgrade gensim

     |████████████████████████████████| 24.2MB 39.1MB/s 
  Found existing installation: gensim 3.6.0
    Uninstalling gensim-3.6.0:
      Successfully uninstalled gensim-3.6.0


In [ ]:
!pip install pyLDAvis

     |████████████████████████████████| 1.7MB 7.6MB/s 
  Created wheel for pyLDAvis: filename=pyLDAvis-3.2.0-py2.py3-none-any.whl size=136694 sha256=3109dd5c0317dbfe2277f2edd1cca8beb6966ede4814065062dfb7e9f32302e2
  Stored in directory: /root/.cache/pip/wheels/5e/62/9d/e2d11b7e09f85508b7be451fa35a2bce4b12c66c10b8bcb182
Successfully built pyLDAvis


In [ ]:
%load_ext google.colab.data_table
# pd.set_option('display.maxcolheight',20)

In [ ]:
from gensim.corpora.dictionary import Dictionary

In [ ]:
from sklearn.tree import DecisionTreeClassifier
from collections import Counter
from sklearn.metrics import confusion_matrix,accuracy_score
import spacy, gensim
import nltk
import re
import matplotlib.pyplot as plt
import sklearn
import pandas as pd
import numpy as np
import seaborn as sns
from tqdm import tqdm
import spacy, gensim
from sklearn.metrics import f1_score
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import LatentDirichletAllocation, TruncatedSVD
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
nlp = spacy.load('en')
import string
from plotly.offline import plot
nltk.download('wordnet')
nltk.download('stopwords')
from sklearn.decomposition.online_lda import LatentDirichletAllocation
from nltk.tokenize import RegexpTokenizer
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from gensim import corpora, models
from collections import Counter
import sklearn.feature_extraction.text as text
from sklearn import decomposition
from sklearn.decomposition import NMF
import gensim
from sklearn.metrics.pairwise import cosine_similarity
from textblob import TextBlob
from nltk.tag import pos_tag
from sklearn.svm import SVC
import heapq
import warnings
from os import listdir
from os.path import isfile, join
from sklearn.preprocessing import label_binarize
from sklearn.multiclass import OneVsRestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.decomposition import NMF
from sklearn.model_selection import train_test_split
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
import re
import numpy as np
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
import spacy
# for plotting
import pyLDAvis
import pyLDAvis.gensim
import matplotlib.pyplot as pl

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


/usr/local/lib/python3.6/dist-packages/sklearn/utils/deprecation.py:144: FutureWarning:

The sklearn.decomposition.online_lda module is  deprecated in version 0.22 and will be removed in version 0.24. The corresponding classes / functions should instead be imported from sklearn.decomposition. Anything that cannot be imported from sklearn.decomposition is now part of the private API.



In [ ]:
# from google.colab import drive
# drive.mount('/content/gdrive')

In [ ]:
with open('fradulent_emails.txt','r', encoding='latin1') as file:
  data=file.read()
print(data[:20000])

FileNotFoundError: ignored

In [ ]:
import email

def extract_messages(df):
    messages = []
    for item in df["message"]:
        # Return a message object structure from a string
        e = email.message_from_string(item)    
        # get message body  
        message_body = e.get_payload()
        messages.append(message_body)
    print("Successfully retrieved message body from e-mails!")
    return messages

In [ ]:
fraud_emails = data.split("From r")
print("Successfully loaded {} spam emails!".format(len(fraud_emails)))

In [ ]:
fraud_bodies = extract_messages(pd.DataFrame(fraud_emails,columns=["message"],dtype=str))
x=np.arange(3978)
fraud_bodies_df = pd.DataFrame(fraud_bodies[1:])
fraud_bodies_df.columns=['Message']
pd.set_option('display.max_colwidth',300)
fraud_bodies_df.head() # you could do print(fraud_bodies_df.head()), but Jupyter displays this nicer for pandas DataFrames

In [ ]:
fraud_ex=[]
for i in fraud_bodies_df['Message']:
  i=''.join(str(i))
  fraud_ex.append(i)

In [ ]:
fraud_df=pd.DataFrame(fraud_ex)
fraud_df.columns=['Message']
fraud_df

In [ ]:
def clean_text(text):
  text=text.lower()
  text = text.lower()
  text = re.sub(r'\[.*?\]', '', text)
  text = re.sub(r'[%s]' % re.escape(string.punctuation), '', text)
  text = re.sub(r'\w*\d\w*', '', text)
  return text

fraud_df=pd.DataFrame(fraud_df.Message.apply(lambda x:clean_text(x)))
fraud_df.head()
fraud_df.to_csv('file.csv',index=False)
# fraud_clean=pd.read_csv('file.csv')
# fraud_clean

In [ ]:
fraud_ex1=[]
for i in fraud_df['Message']:
  i=''.join(str(i))
  fraud_ex1.append(i)
  # print(type(i))

In [ ]:
fraud_df1=pd.DataFrame(fraud_ex1)
fraud_df1.columns=['Message']
fraud_df1

In [ ]:
def lemmatizer(text):
  sent=[]
  doc=nlp(text)
  for word in doc:
    sent.append(word.lemma_)
  return ' '.join(sent)

In [ ]:
lemmatized_corpus=[]
for i in range(len(fraud_df1)):
  text_lemma=lemmatizer(fraud_df1['Message'][i])
  lemmatized_corpus.append(text_lemma)

lemmatized_corpus

In [ ]:
lemmatized_corpus=pd.DataFrame(lemmatized_corpus)
lemmatized_corpus.columns=['Message']
lemmatized_corpus.head()

In [ ]:
def clean_it(text):
  text=re.sub(r'-PRON-','',text)
  text=re.sub(r'\n','',text)
  return text
lemmatized_corpus=pd.DataFrame(lemmatized_corpus.Message.apply(lambda x:clean_it(x)))
lemmatized_corpus['Message'][2]

In [ ]:
# lemmatized_corpus=pd.DataFrame(lemmatized_corpus.Message.apply(lambda x:clean_text(x)))
# lemmatized_corpus

In [ ]:
stop_words=stopwords.words('english')
stop_words.extend(['from','account','bank','transfer','money'])

vectorizer=CountVectorizer(analyzer='word',
                           min_df=3,
                           stop_words='english',
                           lowercase=True,
                           token_pattern='[a-zA-Z0-9]{3,}',
                           max_features=1000,
                           )

data_vectorized=vectorizer.fit_transform(lemmatized_corpus['Message'])
lda_model = LatentDirichletAllocation(n_components=7, # Number of topics
                                      learning_method='online',
                                      random_state=0,       
                                      n_jobs = -1  # Use all available CPUs
                                     )
lda_output = lda_model.fit_transform(data_vectorized)


In [ ]:
lda_model1=gensim.models.LdaMulticore(corpus=corpus,id2word=id2word,num_topics=7,random_state=100,chunksize=100,passes=10,per_word_topics=True)
lda_model1.print_topics()



---











In [ ]:
# import gensim
# from gensim.utils import simple_preprocess
# copy1=lemmatized_corpus
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations
data = lemmatized_corpus.Message.values.tolist()
data_words = list(sent_to_words(data))
print(data_words[:1][0][:30])

['frommr', 'james', 'ngola', 'confidential', 'tel', 'email', 'urgent', 'business', 'assistance', 'and', 'partnership', 'dear', 'friend', 'be', 'dr', 'james', 'ngola', 'the', 'personal', 'assistance', 'to', 'the', 'late', 'congolese', 'president', 'laurent', 'kabila', 'who', 'be', 'assassinate']


In [ ]:
corpus = [id2word.doc2bow(text) for text in data_words]

In [ ]:
# from gensim.corpora import corpora

id2word=corpora.Dictionary(data_words)

coherence_model_lda=CoherenceModel(model=lda_model,texts=data_words,dictionary=id2word,coherence='c_v')
coherence_lda=coherence_model_lda.get_coherence()

print('\nCoherence Score: ',coherence_lda)

In [ ]:
def compute_coherence_values(dictionary, corpus, texts, limit, start=2, step=3):
    """
    Compute c_v coherence for various number of topics

    Parameters:
    ----------
    dictionary : Gensim dictionary
    corpus : Gensim corpus
    texts : List of input texts
    limit : Max num of topics

    Returns:
    -------
    model_list : List of LDA topic models
    coherence_values : Coherence values corresponding to the LDA model with respective number of topics
    """
    coherence_values = []
    model_list = []
    for num_topics in range(start, limit, step):
        model=LdaModel(corpus=corpus, id2word=dictionary, num_topics=num_topics)
        model_list.append(model)
        coherencemodel = CoherenceModel(model=model, texts=texts, dictionary=dictionary, coherence='c_v')
        coherence_values.append(coherencemodel.get_coherence())

    return model_list, coherence_values

In [ ]:
# from gensim.models.ldamodel import Ldamodel

In [ ]:
#@title plotting coherence scores
# dictionary=Dictionary(data_words)
# model_list, coherence_values = compute_coherence_values(dictionary=dictionary, corpus=corpus, texts=data_words, start=2, limit=40, step=6)
# # Show graph
# import matplotlib.pyplot as plt
# limit=40; start=2; step=6;
# x = range(start, limit, step)
# plt.plot(x, coherence_values)
# plt.xlabel("Num Topics")
# plt.ylabel("Coherence score")
# plt.legend(("coherence_values"), loc='best')
# plt.show()

In [ ]:
#@title Function to compute coerence scores
# # supporting function
# def compute_coherence_values(corpus, dictionary, k, a, b):
    
#     lda_model = gensim.models.LdaMulticore(corpus=corpus,
#                                            id2word=dictionary,
#                                            num_topics=k, 
#                                            random_state=100,
#                                            chunksize=100,
#                                            passes=10,
#                                            alpha=a,
#                                            eta=b)
    
#     coherence_model_lda = CoherenceModel(model=lda_model_copy1, texts=data_words, dictionary=id2word, coherence='c_v')
    
#     return coherence_model_lda.get_coherence()

In [ ]:
#@title tried to plot
# import numpy as np
# import tqdm
# grid = {}
# grid['Validation_Set'] = {}
# # Topics range
# min_topics = 2
# max_topics = 11
# step_size = 1
# topics_range = range(min_topics, max_topics, step_size)
# # Alpha parameter
# alpha = list(np.arange(0.01, 1, 0.3))
# alpha.append('symmetric')
# alpha.append('asymmetric')
# # Beta parameter
# beta = list(np.arange(0.01, 1, 0.3))
# beta.append('symmetric')
# # Validation sets
# num_of_docs = len(corpus)
# corpus_sets = [# gensim.utils.ClippedCorpus(corpus, num_of_docs*0.25), 
#                # gensim.utils.ClippedCorpus(corpus, num_of_docs*0.5), 
#                gensim.utils.ClippedCorpus(corpus, num_of_docs*0.75), 
#                corpus]
# corpus_title = ['75% Corpus', '100% Corpus']
# model_results = {'Validation_Set': [],
#                  'Topics': [],
#                  'Alpha': [],
#                  'Beta': [],
#                  'Coherence': []
#                 }
# # Can take a long time to run
# if 1 == 1:
#     pbar = tqdm.tqdm(total=540)
    
#     # iterate through validation corpuses
#     for i in range(len(corpus_sets)):
#         # iterate through number of topics
#         for k in topics_range:
#             # iterate through alpha values
#             for a in alpha:
#                 # iterare through beta values
#                 for b in beta:
#                     # get the coherence score for the given parameters
#                     cv = compute_coherence_values(corpus=corpus_sets[i], dictionary=id2word, 
#                                                   k=k, a=a, b=b)
#                     # Save the model results
#                     model_results['Validation_Set'].append(corpus_title[i])
#                     model_results['Topics'].append(k)
#                     model_results['Alpha'].append(a)
#                     model_results['Beta'].append(b)
#                     model_results['Coherence'].append(cv)
                    
#                     pbar.update(1)
#     pd.DataFrame(model_results).to_csv('lda_tuning_results.csv', index=False)
#     pbar.close()



---



In [ ]:

def show_topics(vectorizer=vectorizer, lda_model=lda_model, n_words=20):
    keywords = np.array(vectorizer.get_feature_names())
    topic_keywords = []
    for topic_weights in lda_model.components_:
        top_keyword_locs = (-topic_weights).argsort()[:n_words]
        topic_keywords.append(keywords.take(top_keyword_locs))
    return topic_keywords

topic_keywords = show_topics(vectorizer=vectorizer, lda_model=lda_model, n_words=20)        

# Topic - Keywords Dataframe
df_topic_keywords = pd.DataFrame(topic_keywords)
df_topic_keywords.columns = ['Word '+str(i) for i in range(df_topic_keywords.shape[1])]
df_topic_keywords.index = ['Topic '+str(i) for i in range(df_topic_keywords.shape[0])]
df_topic_keywords

Word 0    Word 1    Word 2  ...      Word 17       Word 18      Word 19
Topic 0  account     money      bank  ...        owner        dollar  transaction
Topic 1     bank     money       kin  ...   department      indicate      contact
Topic 2     fund  transfer  contract  ...  information  confidential          oil
Topic 3     bank       kin    client  ...      forward     necessary      million
Topic 4      div     money       sir  ...        votre         white       mugabe
Topic 5    money   country   contact  ...         make     president        email
Topic 6     want     money       god  ...      receive         reply         make

[7 rows x 20 columns]

In [ ]:
#Define labels for topics discovered 

In [ ]:
#Getting  Tf-Idf vectorizer for our NMF models 

n_features = 2000
n_components = 7
n_top_words = 20
tfidf_vectorizer = TfidfVectorizer(max_df=0.95, min_df=2,
                                   max_features=n_features,
                                   stop_words='english')
tfidf = tfidf_vectorizer.fit_transform(lemmatized_corpus['Message'])
# nmf = NMF(n_components=n_components, random_state=1, alpha=.1, l1_ratio=.5).fit(tfidf)

In [ ]:
from sklearn.decomposition import NMF
nmf = NMF(n_components=n_components, random_state=1, alpha=.1, l1_ratio=.5).fit(tfidf)

In [ ]:
def show_topics(vectorizer=tfidf_vectorizer, nmf_model=nmf, n_words=20):
    keywords = np.array(vectorizer.get_feature_names())
    topic_keywords = []
    for topic_weights in nmf_model.components_:
        top_keyword_locs = (-topic_weights).argsort()[:n_words]
        topic_keywords.append(keywords.take(top_keyword_locs))
    return topic_keywords

topic_keywords = show_topics(vectorizer=tfidf_vectorizer, nmf_model=nmf, n_words=20)  
# Topic - Keywords Dataframe
df_topic_keywords1 = pd.DataFrame(topic_keywords)
df_topic_keywords1.columns = ['Word '+str(i) for i in range(df_topic_keywords1.shape[1])]
df_topic_keywords1.index = ['Topic '+str(i) for i in range(df_topic_keywords1.shape[0])]
df_topic_keywords1

Word 0   Word 1  ...      Word 18      Word 19
Topic 0           kin     bank  ...         fund        apply
Topic 1        father    money  ...    president     business
Topic 2      contract  foreign  ...          sum         bank
Topic 3          bank      kin  ...  transaction      account
Topic 4  organization  charity  ...       cancer  deteriorate
Topic 5       husband      aid  ...         iraq       ravage
Topic 6       account     bank  ...      capable      million

[7 rows x 20 columns]

In [ ]:
pyLDAvis.enable_notebook(sort=True)
vis = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)

In [ ]:
nmf_output=nmf.transform(tfidf)
nmf_output[2]

array([0.        , 0.09182359, 0.02040282, 0.        , 0.        ,
       0.        , 0.0087394 ])

In [ ]:
#Label NMF topics 

In [ ]:
v=lda_output
v=v*100
len(v)
v[2]

array([8.20341045e-02, 8.19117525e-02, 1.22862895e+01, 8.19518150e-02,
       8.20755580e-02, 8.40164441e+01, 3.36929316e+00])

In [ ]:
from tqdm import tqdm
s=[]
for i in tqdm(range(len(nmf_output))):
  s1=nmf_output[i]/sum(nmf_output[i])
  s.append(s1)

nmf_output=np.array(s)
d=nmf_output
d=d*100
len(d)
d[2]

100%|██████████| 3977/3977 [00:00<00:00, 178165.52it/s]


array([ 0.        , 75.90870778, 16.86660321,  0.        ,  0.        ,
        0.        ,  7.22468901])

In [ ]:
def normalize(df):
  result=df.copy()
  for feature_name in df.columns:
    max_value=df[feature_name].max()
    min_value=df[feature_name].min()

    if max_value - min_value !=0:
      result[feature_name]=(df[feature_name]-min_value) / (max_value - min_value) 
    else:
      result[feature_name]=0
  return result

In [ ]:
LDA_df=pd.DataFrame(v,columns=df_topic_keywords.T.columns)
NMF_df=pd.DataFrame(d,columns=df_topic_keywords1.T.columns)

LDA_normalized=normalize(LDA_df)
NMF_normalized=normalize(NMF_df)

In [ ]:
LDANMF=pd.concat([NMF_normalized,LDA_normalized],axis=1)
LDANMF.head()

Topic 0   Topic 1   Topic 2  ...   Topic 4   Topic 5   Topic 6
0  0.000000  0.607890  0.081422  ...  0.027434  0.808107  0.000721
1  0.004709  0.431455  0.361388  ...  0.000654  0.514086  0.000784
2  0.000000  0.759087  0.168666  ...  0.000674  0.843402  0.033819
3  0.000000  0.759087  0.168666  ...  0.000674  0.843402  0.033819
4  0.000000  0.515904  0.026533  ...  0.000479  0.793503  0.110633

[5 rows x 14 columns]

In [ ]:
def compute_confidence_score(similarityList):
  similarityscores=set(similarityList)
  highest=max(similarityscores)

  similarityscores.remove(highest)

  if(len(similarityscores)==0):
    return 0
  
  second_highest=max(similarityscores)
  return ((highest - second_highest)/(highest))*100

In [ ]:
dominant_topic=np.argmax(LDANMF.values,axis=1)

LDANMF['confidence']=LDANMF.apply(lambda row:compute_confidence_score(row),axis=1)
LDANMF['dominant_topic']=dominant_topic

In [ ]:
final=pd.concat([lemmatized_corpus,LDANMF[['dominant_topic','confidence']]],axis=1)
final

Message  ...  confidence
0     frommr james ngola  confidential tel  email  urgent business assistance and partnership  dear friend  i be   dr james ngola the personal assistance to the late congolese president laurent kabila who be assassinate by  body guard on   jan  the incident occur in  presence while  be hold meeting wi...  ...   93.265776
1     dear friend  i be mr ben suleman a custom officer and work as assistant controller of the custom and excise department of the federal ministry of internal affairs station at the murtala mohammed international airport ikeja lagosnigeria  after the sudden death of the former head of state of niger...  ...   95.715954
2     from  royal majesty hrm crown ruler of eleme kingdom  chief daniel eleme phd eze   of elemeemail    attentionpresidentceo sir madam  this letter may surprise  because  have meet  neither in person nor by correspondence but i believe   be one day that  get to know somebody either in  physical or ...  ...   92.971650
3     from  royal majesty hrm crown ruler of eleme kingdom  chief daniel eleme phd eze   of elemeemail    attentionpresidentceo sir madam  this letter may surprise  because  have meet  neither in person nor by correspondence but i believe   be one day that  get to know somebody either in  physical or ...  ...   92.971650
4     dear sir    be with a heart full of hope that i write to seek  help in respect of the context below i be mrs maryam abacha the former first lady of the former military head of state of nigeria general sani abacha whose sudden death occur on   of june   as a result of cardiac arrest heart attack ...  ...   93.387475
...                                                                                                                                                                                                                                                                                                           ...  ...         ...
3972  atten  dear   i have pay the fee for  cheque draftbecause the manager of ecobank  benin tell  that before the check will get to  that  willexpire  so i tell  to cash    however all the necessary arrangement  of deliver the   in cash be make with   global max   ship  courier company this be the i...  ...   93.564511
3973                                                                                                                                                                                                                                                                                                               ...         NaN
3974                                                                                                                                                                                                                                                                                                               ...         NaN
3975   beloved in the lord jesus christ please endeavour to use  for the  child of god   name be mother doris killam   old woman from united states of  america i be married to engineer pitt killam who till  death work  with willbro a us oil engineering firm here in nigeria  be  marry for thirteen   ye...  ...   92.886070
3976                                                                                                                                                                                                                                                                                                               ...         NaN

[3977 rows x 3 columns]